# Upload mangrove extent to GCS and as an asst to GEE

This notebook gets mangrove extent data, uploads to GCS, and creates an earth engine image collection asset.  
These are the steps:  
* We first need to create a single tiff per year of mangrove extent data.
* We then upload the tiffs to GCS.
* We then create an earthengine image collection asset.
* We then upload each image as an asset to GEE.
* Finally make the data also publicly available in Zenodo.

## Setup

In [1]:
import os
from pathlib import Path
import urllib.parse
import geemap
import ee
import tarfile

%run utils.ipynb

In [2]:
# Trigger the authentication flow.
ee.Authenticate()

# Initialize the library.
ee.Initialize()

Enter verification code: 4/1AdQt8qgEYq6zKmp0nXOq4Dg-FL6UdF_PHh_YCTIix1VX2RVnDyDwg9p9O70

Successfully saved authorization token.


### Set Cloud credentials (could be done through and env file)

In [3]:
# WARNING: Don't forget to auth to google cloud platform
# gcloud auth application-default login --no-launch-browser --project=mangrove-atlas-246414

### Set Variables for GCS and GEE

In [4]:
#  FIXME: This will depends from where the notebook kernel is running so be careful
WORK_DIR =Path(os.getcwd())
BASE_DIR = f'{WORK_DIR.parents[3]}/datasets'

# @TODO: Add expected data files source as an environment variable.
assert BASE_DIR == '/home/jovyan/work/datasets', f'{BASE_DIR} is not the correct directory'

# variables
data_version = 'v3'
dataset = 'mangrove_aboveground_biomass'

# Set the Google Cloud params
gc_project_id = "mangrove-atlas-246414"
gcs_bucket = f'mangrove_atlas'
gcs_prefix = f"gs://{gcs_bucket}"

# raw data source
raw_dataset_name = 'agb_mng_gmw_v3_tif.tar.gz'
base_source_data_url = f'https://www.dropbox.com/sh/ruk6m9btrkqb73b/AAC8lWSe7nOfDGzrapMR_uqRa?dl=0'
gcs_source_data_url = f'{gcs_prefix}/mangrove-properties/{raw_dataset_name}'

raw_local_folder = Path(f'{BASE_DIR}/raw/{dataset}')
raw_local_folder.mkdir(parents=True, exist_ok=True)

# Image Collection Information
data_year_range = [1996, 2007, 2008, 2009, 2010, 2015, 2016, 2017, 2018, 2019, 2020]
ee_image_collection = f'projects/global-mangrove-watch/mangrove-properties/{dataset}-{data_version}'

no_data_values = [0]
pyramiding = 'MEAN'


In [5]:
description = f"""
## Methodology

This dataset characterizes the global distribution, biomass, and canopy height of mangrove-forested wetlands based on remotely sensed and in situ field measurement data. 
Estimates of (1) mangrove aboveground biomass (AGB), for the nominal year 2000 were derived across a 30-meter resolution global mangrove ecotype extent map using remotely-sensed 
canopy height measurements and region-specific allometric models. Also provided are (4) in situ field measurement data for selected sites across a wide variety of forest 
structures (e.g., scrub, fringe, riverine and basin) in mangrove ecotypes of the global equatorial region. Within designated plots, selected trees were identified to 
species and diameter at breast height (DBH) and tree height was measured using a laser rangefinder or clinometer. Tree density (the number of stems) can be estimated for 
each plot and expressed per unit area. These data were used to derive plot-level allometry among AGB, basal area weighted height (Hba), and maximum canopy height (Hmax) 
and to validate the remotely sensed estimates.  

Spatially explicit maps of mangrove canopy height and AGB derived from space-borne remote sensing data and in situ measurements can be used to assess local-scale 
geophysical and environmental conditions that may regulate forest structure and carbon cycle dynamics. Maps revealed a wide range of canopy heights, including maximum 
values (> 62 m) that surpass maximum heights of other forest types.

### {', '.join(list(map(str, data_year_range[:-1])))} and {data_year_range[-1]} maps of mangrove aboveground biomass (AGB)

For the full documentation, please see the source [methodology](https://daac.ornl.gov/CMS/guides/CMS_Global_Map_Mangrove_Canopy.html).
"""

In [22]:
extent_collection_properties = ImageCollectionProperties(
    name = 'Mangrove aboveground biomass (AGB)',
    version = data_version,
    creator = "Global Mangrove Watch (GMW): Aberystwyth University/soloEO/Wetlands International/UNEP-WCMC/JAXA/DOB Ecology",
    description = description,
    identifier = "",
    keywords = "Erosion; Coasts; Natural Infrastructure; Biodiversity; Blue Carbon; Forests; Mangroves; Landcover",
    citation = "Simard, M., T. Fatoyinbo, C. Smetanka, V.H. Rivera-monroy, E. Castaneda, N. Thomas, and T. Van der stocken. 2019. Global Mangrove Distribution, Aboveground Biomass, and Canopy Height. ORNL DAAC, Oak Ridge, Tennessee, USA. https://doi.org/10.3334/ORNLDAAC/1665",
    license = "https://creativecommons.org/licenses/by/4.0/",
    url = "https://daac.ornl.gov/cgi-bin/dsviewer.pl?ds_id=1665",
    language = "en", 
    altName = "Mangrove aboveground biomass (AGB), Version 3.0",
    distribution = "",
    variableMeasured = "Mangrove aboveground biomass (AGB)",
    units = "t/ha",
    spatialCoverage = "Global tropics",
    temporalCoverage = ','.join(map(str, data_year_range)),
    dataLineage = "Raster data supplied as tilesets per year, each tilset was combined, and added to Google earth engine as multi-temporal ImageCollection."
)

In [23]:
def generate_manifests(year):
    files = [blob.name for blob in list_gcs(bucket_name = gcs_bucket, 
                    dir_path = f'ee_import_data/{dataset}/agb_mng_mjr_{year}_tif', file_pattern = '*.tif') if blob.name.endswith('.tif')]
    manifest = GEEManifest(
            path = Path(f'{BASE_DIR}/processed/manifest/agb_mng_mjr_{data_version}_{year}'),
            name = f"projects/earthengine-legacy/assets/{ee_image_collection}/gmw_{dataset}_{year}",
            tilesets = [ Tilesets(
                sources = [Sources(uris = [f"{gcs_prefix}/{file}"]) for file in files],
                    )
                ],
            start_time = f'{year}-01-01T00:00:00Z',
            end_time = f'{year}-12-31T00:00:00Z',
            uri_prefix = f"",
            properties = ImageProperties(
                band_nodata_values = no_data_values[0],
                band_pyramiding_policies = pyramiding,
                band_names = 'above ground biomass (agb)',
                year = year,
            ),
            bands = [{"id": "agb",
                    "tileset_band_index": 0}],
            pyramiding_policy = pyramiding,
            missing_data = {'values': no_data_values}

        )
    return manifest

In [18]:
def extract_path_from_zip(path_zip: Path):
    # Extract all the contents of zip file in current directory
    for item in path_zip.iterdir():
        if '.tar.gz' in item.name:
            with tarfile.open(item.as_posix(), 'r') as zipObj:
                zipObj.extractall(path_zip)
            
            item.unlink()

In [9]:
def rm_tree(pth: Path):
    for child in pth.iterdir():
        if child.is_file():
            child.unlink()
        else:
            rm_tree(child)
    pth.rmdir()

In [16]:
files = list(list_gcs(bucket_name = gcs_bucket, dir_path = 'mangrove-properties', file_pattern = raw_dataset_name))
files

INFO:root:Searching mangrove-properties/agb_mng_gmw_v3_tif.tar.gz


[<Blob: mangrove_atlas, mangrove-properties/, 1563369444139420>,
 <Blob: mangrove_atlas, mangrove-properties/agb_mng_gmw_v3_tif.tar.gz, 1660149522699737>,
 <Blob: mangrove_atlas, mangrove-properties/hchm_mng_gmw_v3_tif.tar.gz, 1660149526790250>,
 <Blob: mangrove_atlas, mangrove-properties/mangrove-soil-organic-carbon_version-0-2_1996--2016_description.md, 1594128267403391>,
 <Blob: mangrove_atlas, mangrove-properties/mangroves_SOC30m_0_100cm.jsonld, 1591393382823623>,
 <Blob: mangrove_atlas, mangrove-properties/mangroves_SOC30m_0_100cm.zip, 1591779593619314>]

### Get the raw files locally

In [37]:
copy_folder_gcs(gcs_source_data_url, raw_local_folder)

Copying gs://mangrove_atlas/GMW v3.14 geotiffs/gmw_v3_1996_gtiff.zip...
Resuming download for /home/jovyan/work/datasets/raw/mangrove_extent/gmw_v3_1996_gtiff.zip
Copying gs://mangrove_atlas/GMW v3.14 geotiffs/gmw_v3_2008_gtiff.zip...
Copying gs://mangrove_atlas/GMW v3.14 geotiffs/gmw_v3_2007_gtiff.zip...
Resuming download for /home/jovyan/work/datasets/raw/mangrove_extent/gmw_v3_2008_gtiff.zip
Copying gs://mangrove_atlas/GMW v3.14 geotiffs/gmw_v3_2009_gtiff.zip...
Resuming download for /home/jovyan/work/datasets/raw/mangrove_extent/gmw_v3_2007_gtiff.zip
Resuming download for /home/jovyan/work/datasets/raw/mangrove_extent/gmw_v3_2009_gtiff.zip
Copying gs://mangrove_atlas/GMW v3.14 geotiffs/gmw_v3_2010_gtiff.zip...
Resuming download for /home/jovyan/work/datasets/raw/mangrove_extent/gmw_v3_2010_gtiff.zip
Copying gs://mangrove_atlas/GMW v3.14 geotiffs/gmw_v3_2015_gtiff.zip...
Copying gs://mangrove_atlas/GMW v3.14 geotiffs/gmw_v3_2016_gtiff.zip...
Copying gs://mangrove_atlas/GMW v3.14 geo

### Extract them and reupload to GCS in the ee_import_data folder

In [19]:
extract_path_from_zip(raw_local_folder)

folder_unziped = [x for x in raw_local_folder.iterdir() if x.is_dir()]

In [20]:
for folder in folder_unziped:
    copy_folder_gcs(folder, f'{gcs_prefix}/ee_import_data/{dataset}/')

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N08E122_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N03E101_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S25E113_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S03W081_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N17W102_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S33E137_agb_gmw_v314_mng_mjr_2009.tif [Content-Typ

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S02E110_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S35E151_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S01W092_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N04W010_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N23W084_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S15W039_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N00E109_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S11E039_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N14W061_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S32E029_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S07E112_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N17W067_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/j

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N18W067_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S03E124_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N26E128_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N06E126_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N16W017_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N09W076_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S08E156_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N16W087_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N15E120_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S05E131_agb_gmw_v314_mng_mjr_2009.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/S21E116_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/N32W065_agb_gmw_v314_mng_mjr_2009.tif [Content-Type=image/tiff]

...

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N15W089_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S17E038_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N04E100_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S19E044_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N05W055_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S21E118_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N02E099_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S09E137_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N21W082_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N24E056_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N01E117_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N05W058_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying f

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N21W073_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S15W172_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S38E176_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N18W072_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N23W098_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S08E012_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N07E124_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N15W097_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S09E158_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N22W078_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S11E151_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S04E107_agb_gmw_v314_mng_mjr_2020.tif

Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N24E037_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N16W086_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S02E135_agb_gmw_v314_mng_mjr_2020.tif [Content-Type=image/tiff]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N12W084_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/N04E108_agb_gmw_v314_mng_mjr_2020.tif.aux.xml [Content-Type=application/xml]...
Copying file:///home/jovyan/work/datasets/raw/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/S15E124_agb_gmw_v314_mng_mjr_2020.tif [Content-Typ

#### Clean up the raw data locally as this is expensive in terms of space.

In [21]:
rm_tree(raw_local_folder)

#### Generate manifests for each year that represent an image in the image collection

In [24]:
list_of_manifests = [generate_manifests(year) for year in data_year_range]

INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_1996_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2007_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2008_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2009_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2010_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2015_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2016_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2017_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2018_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2019_tif/*.tif
INFO:root:Searching ee_import_data/mangrove_aboveground_biomass/agb_mng_mjr_2020_tif/*.tif

#### Create the image collection asset and upload the images to GEE

In [25]:
createImageCollection(ee_asset_path = ee_image_collection,
                        properties = extent_collection_properties, 
                        image_list = list_of_manifests)

INFO:root:Created image collection projects/global-mangrove-watch/mangrove-properties/mangrove_aboveground_biomass-v3
INFO:root:Task created
INFO:root:Upload image projects/earthengine-legacy/assets/projects/global-mangrove-watch/mangrove-properties/mangrove_aboveground_biomass-v3/gmw_mangrove_aboveground_biomass_1996


Started upload task with ID: I5MTLTZKSDQ4RIHMUCRGYS43


INFO:root:Task created
INFO:root:Upload image projects/earthengine-legacy/assets/projects/global-mangrove-watch/mangrove-properties/mangrove_aboveground_biomass-v3/gmw_mangrove_aboveground_biomass_2007


Started upload task with ID: QUDJHT2WMLQT74AIU23YJ6AU


INFO:root:Task created
INFO:root:Upload image projects/earthengine-legacy/assets/projects/global-mangrove-watch/mangrove-properties/mangrove_aboveground_biomass-v3/gmw_mangrove_aboveground_biomass_2008


...

Started upload task with ID: X7JRVD22LY454OXI5GHHGL7T


INFO:root:Task created
INFO:root:Upload image projects/earthengine-legacy/assets/projects/global-mangrove-watch/mangrove-properties/mangrove_aboveground_biomass-v3/gmw_mangrove_aboveground_biomass_2019


Started upload task with ID: BXRDZVRAEHFDYWUMGT7YVLUB


INFO:root:Task created
INFO:root:Upload image projects/earthengine-legacy/assets/projects/global-mangrove-watch/mangrove-properties/mangrove_aboveground_biomass-v3/gmw_mangrove_aboveground_biomass_2020


Started upload task with ID: NC3BIGRQ4O3VHJJOOQZT22PF


#### If we need to add new years to the image collection, we can do that by adding new manifests to the image collection asset.

In [108]:
addImagesToCollection(ee_image_collection, list_of_manifests[0:1])

INFO:root:Task created
INFO:root:Upload image projects/earthengine-legacy/assets/projects/global-mangrove-watch/land-cover/mangrove-extent-test/gmw_v3_1996


Started upload task with ID: CJXPIRIMZJL6MGZ2US6RD3CH


In [112]:
# Check task status
!earthengine task list --status RUNNING

CJXPIRIMZJL6MGZ2US6RD3CH  Upload        Ingest image: "projects/earthengine-lega..  RUNNING    ---


In [ ]:
# Check ImageCollection properties
!earthengine asset info {ee_asset_path}